# Kaggle Halite Episode Service API Client

__Purpose is to make an API and program to fetch data from Kaggle__

## Kaggle Halite API Endpoints

Kaggle's Sam Harris release an API to pull Halite match data from games hosted on Kaggle.
- Post documenting API: https://www.kaggle.com/c/halite/discussion/164932
- API Wrapper here: https://github.com/Kaggle/kaggle-environments/blob/master/kaggle_environments/api.py
- API service is located at: https://www.kaggle.com/requests/EpisodeService/

#### GetEpisodeReplay Endpoint

- URL: 'https://www.kaggle.com/requests/EpisodeService/GetEpisodeReplay'
- Verb: Post
- Schema: JSON
- JSON Payload: {"EpisodeId": episode_id} # int

#### ListEpisodes Endpoint

- URL: 'https://www.kaggle.com/requests/EpisodeService/ListEpisodes'
- Verb: Post
- Schema: JSON
- JSON Payload:
    - {"Ids": episode_ids} # List[int]
    - {"TeamId": team_id} # int
    - {"SubmissionId": submission_id} # int

## Kaggle Halite API Client Implementation

In [1]:
__version__ = '0.0.1'


from urllib.parse import urljoin
import inspect
import requests
import json as json_lib

class KaggleClient(object):
    """ A Kaggle Halite Episode Service API wrapper. """
    
    def __init__(self):
        self.requester = self.Requester()
        self._attach_endpoints()
        
    def _attach_endpoints(self):
        """ Generate and attach endpoints """
        for name, endpoint in inspect.getmembers(self):
            if (inspect.isclass(endpoint) 
                and issubclass(endpoint, self._Endpoint) 
                and endpoint is not self._Endpoint):
                endpoint_instance = endpoint(self.requester)
                setattr(self, endpoint.name, endpoint_instance)
    
    class Requester(object):
        """ An object for making API requests """
        
        def GET(self, url, params=None, json=None):
            if None is params:
                params = dict()
            if None is json:
                json = dict()
    
            params.setdefault('datatype', 'json')
            response = requests.post(url, params=params, json=json)
            if 200 != response.status_code:
                error = 'HTTPError: {}'.format(response.status_code)
                return {'success': False, 'error': error}
            try:
                return response.json()
            except ValueError as err:
                return {'success': False, 'error': err}
        
    class _Endpoint(object):
        """ Base class of an endpoint """
        url = 'https://www.kaggle.com/requests/EpisodeService/'
        
        def __init__(self, requester):
            self.requester = requester            
        
        def _GET(self, path, params=None, json=None):
            request_url = urljoin(self.url, path)
            #print(f'url: {self.url}, request_url: {request_url}, path: {path}')
            return self.requester.GET(request_url, params, json)
    
    class Replay(_Endpoint):
        name = 'replay'
        
        def episode(self, episode_id, params=None):
            json = {"EpisodeId": episode_id}
            resp = self._GET('GetEpisodeReplay', params, json)
            resp['result']['replay'] = json_lib.loads(resp['result']['replay'])
            return resp
        
    class Episodes(_Endpoint):
        name = 'episodes'

        def episodes(self, episode_ids, params=None):
            json = {'Ids': episode_ids}
            return self._GET('ListEpisodes', params, json)
        
        def team(self, team_id, params=None):
            json = {'TeamId': team_id}
            return self._GET('ListEpisodes', params, json)
        
        def submission(self, submission_id, params=None):
            json = {'SubmissionId': submission_id}
            return self._GET('ListEpisodes', params, json)

## How-to Use Implementation

In [2]:
TEAM_ID = 5118174

In [3]:
api = KaggleClient()

Get Team Endpoint Response.

In [4]:
team_ep_resp = api.episodes.team(TEAM_ID)

In [5]:
team_ep_resp['result']['episodes'][0]['id']

1052028

Get Episode Endpoint Response.

In [6]:
episode_ids = [team_ep_resp['result']['episodes'][i]['id'] for i in range(10) if len(team_ep_resp['result']['episodes']) >= i]

In [7]:
episodes_ep_resp = api.episodes.episodes(episode_ids)

Get Submission Endpoint Response.

In [8]:
submission_ids = [episodes_ep_resp['result']['episodes'][i]['agents'][0]['submission']['id'] for i in range(10) if len(team_ep_resp['result']['episodes']) >= i]

In [9]:
submission_ep_resp = api.episodes.submission(submission_ids[0])

Get Replay Endpoint Response

In [10]:
replay_ep_resp = api.replay.episode(episode_ids[0])

In [11]:
replay_ep_resp

{'result': {'replay': {'configuration': {'actTimeout': 6,
    'agentExec': 'LOCAL',
    'agentTimeout': 12,
    'collectRate': 0.25,
    'convertCost': 500,
    'episodeSteps': 400,
    'maxCellHalite': 500,
    'moveCost': 0,
    'regenRate': 0.02,
    'runTimeout': 1200,
    'size': 21,
    'spawnCost': 500,
    'startingHalite': 24000},
   'description': 'The game of space salt.',
   'id': '30488ca8-b056-11ea-9090-0242ac130206',
   'name': 'halite',
   'rewards': [479, 81, 825, 299],
   'schema_version': 1,
   'specification': {'action': {'additionalProperties': {'description': 'Key: uid of the asset. Value: action. SPAWN for shipyards, remaining for ships.',
      'enum': ['CONVERT', 'SPAWN', 'NORTH', 'SOUTH', 'EAST', 'WEST']},
     'default': 0,
     'description': 'Actions taken per asset (ship or shipyard).',
     'type': 'object'},
    'agents': [1, 2, 4],
    'configuration': {'actTimeout': {'default': 6,
      'description': 'Maximum runtime (seconds) to obtain an action from